In [1]:
#!/usr/bin/env python
# -*- coding: utf-8 -*-

from topogram_client import TopogramAPIClient

from csv import DictReader
import os
import json
import pymongo
#import musicbrainzngs
import arrow
from datetime import datetime
from pymongo import MongoClient
from collections import defaultdict
from dateutil import parser
from datetime import timedelta
import pickle
import time
from slugify import slugify

In [2]:
import colorsys
def get_N_HexCol(N=20):

    HSV_tuples = [(x*1.0/N, 0.5, 0.5) for x in xrange(N)]
    hex_out = []
    for rgb in HSV_tuples:
        rgb = map(lambda x: int(x*255),colorsys.hsv_to_rgb(*rgb))
        hex_out.append("".join(map(lambda x: chr(x).encode('hex'),rgb)))
    return hex_out

In [3]:
def create_topogram(title, nodes, edges):

    print "Creating topogram '%s'"%title

    try :
        r = topogram.create_topogram(title)
    except ValueError:
        print '> Topogram already exists'
        r = topogram.get_topogram_by_name(title)
    print r
    topogram_ID = r["data"]["_id"]
    print "topogram ID : %s"%topogram_ID

    # get and backup existing nodes and edges
    existing_nodes = topogram.get_nodes(topogram_ID)["data"]
    existing_edges = topogram.get_edges(topogram_ID)["data"]

    # clear existing graph
    if len(existing_nodes):
        topogram.delete_nodes([n["_id"] for n in existing_nodes])
        print "%s nodes deleted"%len(existing_nodes)
    if len(existing_edges):
        topogram.delete_edges([n["_id"] for n in existing_edges])
        print "%s edges deleted"%len(existing_edges)

    r = topogram.create_nodes(topogram_ID, nodes)
    print r
    print "%s nodes created."%len(r["data"])
    r = topogram.create_edges(topogram_ID, edges)
    print "%s edges created."%len(r["data"])

    print "done. Topogram has been updated. Check it at %s/topograms/%s"%(TOPOGRAM_URL, topogram_ID)



In [9]:
import math
# setup mongo
client = MongoClient()
db = client["bandstour"]
bandsintown =  db["minedArtists"]

# credentials
TOPOGRAM_URL = "https://app.topogram.io"
USER = "gregory.bahde@laposte.net"
PASSWORD = "matrix"

# data
title = "Foo Fighters bandstour 0.1"
my_nodesdict = {}
my_nodes= []
my_edges = []
my_edgesdict = {}

# date parsing
DATETIME_FORMAT = '%Y-%m-%dT%H:%M:%S'
DATETIME_FORMAT_FOR_MSBNZ ='%Y-%m-%d'

#retrieve trip coords for each artist
dict_coords={}
colors_for_nodes_and_edges = get_N_HexCol()

for artist in db.minedArtists.find({"totalKm": {"$gte": 2000000}}) :
 title = artist["name"]   
 if os.path.exists("./bands_dicts/"+artist["name"]+".obj")==True:
        print "SKIPPED",artist["name"]
        pass
 else:
    my_nodesdict = {}
    my_nodes= []
    my_edges = []
    my_nodesdictList=[]
    my_edgesdict = {}
    #colors_for_nodes_and_edges = get_N_HexCol()
    
    print artist["name"]
    #print artist
    dates_coords = []
    dates = artist.get("gigs")
    tours = artist.get("tours")    
    singlegigs = artist.get("singleGigs")
    dateini=0
    touring=0
    tour_indice=0
    tmpOLDgig ={}
    for tour in tours:
     tour_color = "#"+colors_for_nodes_and_edges[tour_indice % 20]
     #print tour_color
     #print tour
     gig_indice =0
     dates = tour.get("gigs")
     for date in dates:
        #print date.get("datetime")
        venue = date.get("venue")
        latitude = venue.get("latitude")
        longitude = venue.get("longitude")
        #print venue
        ###concat key
        idd= slugify(venue["name"])+str(int(venue["latitude"]))+str(int(venue["longitude"]))
        
        if idd not in my_nodesdict:
            
            node = {
                    "id" : idd,
                    "name" : slugify(venue["name"]),
                    "lat" : float(venue["latitude"]),
                    "lng" : float(venue["longitude"]),
                    "weight" : float(1),
                    "start" : date.get("datetime").isoformat(),
                    "end" : (date.get("datetime")+timedelta(days=1)).isoformat(),
                    "color" : tour_color,
                    "notes" : "name : "+slugify(venue["name"])+"  \nlat : "+str(float(venue["latitude"]))+"  \nlng :"+str(float(venue["longitude"]))+"  \n weight :"+str(1)+"  \nstart : "+str(date.get("datetime").isoformat())+"  \nend : "+str((date.get("datetime")+timedelta(days=1)).isoformat())+"  \ncolor :"+str(tour_color)
                    }
        else:
                
                node = {
                    "id" : idd,
                    "name" : slugify(venue["name"]),
                    "lat" : float(venue["latitude"]),
                    "lng" : float(venue["longitude"]),
                    "weight" : math.sqrt(float(my_nodesdict[idd]["data"].get("weight"))+1) ,
                    "start" : my_nodesdict[idd]["data"].get("start"),
                    "end" : (date.get("datetime")+timedelta(days=1)).isoformat(),
                    "color" : tour_color,
                    "notes" : "name : "+slugify(venue["name"])+"  \nlat : "+str(float(venue["latitude"]))+"  \nlng :"+str(float(venue["longitude"]))+"  \n weight :"+str((float(my_nodesdict[idd]["data"].get("weight"))+1))+"  \nstart : "+str(my_nodesdict[idd]["data"].get("start"))+"  \nend : "+(date.get("datetime")+timedelta(days=1)).isoformat()+"  \ncolor :"+tour_color
                    
                    }
        if dateini == 0:
                dateini =1
        else:
                #print my_nodes[-1]["data"]["id"]
                #print dates[gig_indice-1]["distanceToNextGig"]
                notesE=""
                notesE+="distance : "
                try: 
                    notesE+=str(dates[gig_indice]["distanceToNextGig"])
                except KeyError:
                    notesE+="dates[gig_indice][distanceToNextGig] NOT AVAILABLE"
                notesE+=" km  \n"
                notesE+="source : "
                notesE+=str(my_nodes[-1]["data"]["id"])
                notesE+="  target : "
                notesE+=str(node["id"])
                notesE+="  \ndatesource : "
                notesE+=dates[gig_indice -1]["datetime"].isoformat()
                notesE+="  \ndatetarget : "
                notesE+=dates[gig_indice]["datetime"].isoformat()
                notesE+="  \ngroup: "
                notesE+=str(tour_indice)
                #notesE+=
                
                
                #print gig_indice
                edge = {
                    "source" : my_nodes[-1]["data"]["id"],
                    "target" : node["id"],
                    "color" :  tour_color,
                    # "notes" : "distance : "+str(round(dates[gig_indice]["distanceToNextGig"],2))+" km  \n"+"source : "+my_nodes[-1]["data"]["id"]+"  target : "+node["id"]+"  \ndatesource : "+dates[gig_indice -1]["datetime"].isoformat()+"  \ndatetarget : "+dates[gig_indice]["datetime"].isoformat()+"  \ngroup:"+str(tour_indice),
                    "notes" : notesE,
                    #"weight" : float(e["weight"]),
                    "start" : dates[gig_indice -1]["datetime"].isoformat(),
                    "end" : dates[gig_indice]["datetime"].isoformat(),
                    #"group" : str(tour_indice)
                    
                }
                #print edge
                my_edges.append({ "data" : edge })
        my_nodes.append({ "data" : node })   
        my_nodesdict[node["id"]]= { "data" : node }
        gig_indice+=1
    #print my_nodes
    #print "<=============================================>"
    #print my_nodesdict
    #print "<=============================================>"
    #print my_edges
     tour_indice +=1
        #print "coords",latitude,"/",longitude
    for key, value in my_nodesdict.iteritems():
            my_nodesdictList.append(value)
    
    #ADDING EDGES WEIGHT HERE
    
    terp= map(lambda x : str(sorted([x["data"]["source"],x["data"]["target"]])),my_edges)
    
    #print terp
    from collections import Counter
    c= Counter()
    for ter in terp:
        c[ter]+=1
    #print c
    for edge in my_edges:
        if str(sorted([edge["data"]["source"],edge["data"]["target"]])) not in terp:
            print "BUG!!!!"
        else:
            if edge["data"]["source"] == edge["data"]["target"]:
                #print c[str(sorted([edge["data"]["source"],edge["data"]["target"]]))]
                edge["data"]["notes"]+="  \ncounted"+str(c[str(sorted([edge["data"]["source"],edge["data"]["target"]]))])+"  times"
                edge["data"]["weight"]= float(1)
                #print "a"
            else:
                edge["data"]["notes"]+="  \ncounted"+str(c[str(sorted([edge["data"]["source"],edge["data"]["target"]]))])+"  times"
                edge["data"]["weight"]= float(c[str(sorted([edge["data"]["source"],edge["data"]["target"]]))])
                #print "b"
    #print my_edges
    
    with open("./bands_dicts/"+artist["name"]+".obj", 'wb') as handle:
                            pickle.dump([artist["name"]+"/BETA_0.3",my_nodesdictList,my_edges], handle, protocol=pickle.HIGHEST_PROTOCOL)    


Tiësto
Infected Mushroom
Dubfire
Cosmic Gate
Mark Knight
NERVO
Laidback Luke
Jazz
Chuckie
Markus Schulz
Legends
Ferry Corsten
Steve Aoki


In [5]:
# credentials
TOPOGRAM_URL = "http://localhost:3000"
USER = "gregory.bahde@laposte.net"
PASSWORD = "matrix"

In [6]:
print len(my_nodesdict)

527


In [7]:
# connect to the topogram instance (pass debug=True params for more info )
topogram = TopogramAPIClient(TOPOGRAM_URL) #, debug=True)

# create a new user
try :
    topogram.create_user(USER, PASSWORD)
except ValueError:
    print "> User has already been created."

# login a new user if needed
resp_user_login = topogram.user_login(USER, PASSWORD)
print resp_user_login

assert(resp_user_login["status"] == "success")
assert(resp_user_login["status_code"] == 200)


ERROR:topogram-client:403 Unauthorized request


> User has already been created.
{u'status': u'success', 'status_code': 200, u'data': {u'authToken': u'3VcIvDJJpgzz1cbqv-0WoDGnDXeP_wJKhxSPYXMFrfU', u'userId': u'MSreQEjksjoK2igp5'}}


In [10]:
nodestop=[]
edgestop=[]
tit=[]
import glob, os

print os.getcwd()

for subdir, dirs, files in os.walk("./bands_dicts"): 
 for file in files:
  if file.endswith('.obj') == True:  
    with open(os.path.join(subdir, file), 'rb') as handle:
          temp= pickle.load( handle)
    #print 
    tit=temp[0].encode("utf-8")
    edgestop=temp[2]
    nodestop=temp[1]
    print edgestop
    while True:
        try:
            #print
            create_topogram(tit, nodestop, edgestop)
        except TypeError:
            continue
        break
        

ERROR:topogram-client:500 - Error : A topogram with the same name already exists


/home/goonieb/gitrep/bandstour/5_visualizer/topogram-api-clientFOR_TOPO_FROM_BANDSTOUR
[{'data': {'end': '2010-09-17T23:00:00', 'target': 'set25-80', 'weight': 1.0, 'source': 'set25-80', 'color': '#7f3f3f', 'notes': 'distance : 328.599454 km  \nsource : set25-80  target : set25-80  \ndatesource : 2010-09-03T23:00:00  \ndatetarget : 2010-09-17T23:00:00  \ngroup: 0  \ncounted1  times', 'start': '2010-09-03T23:00:00'}}, {'data': {'end': '2010-11-11T22:00:00', 'target': 'club-firestone28-81', 'weight': 1.0, 'source': 'set25-80', 'color': '#7f523f', 'notes': 'distance : 127.562425 km  \nsource : set25-80  target : club-firestone28-81  \ndatesource : 2010-11-23T19:00:00  \ndatetarget : 2010-11-11T22:00:00  \ngroup: 1  \ncounted1  times', 'start': '2010-11-23T19:00:00'}}, {'data': {'end': '2010-11-12T21:00:00', 'target': 'hawaiian-village27-82', 'weight': 1.0, 'source': 'club-firestone28-81', 'color': '#7f523f', 'notes': 'distance : 335.02856 km  \nsource : club-firestone28-81  target : hawai

527 nodes deleted
778 edges deleted
{u'status': u'success', 'status_code': 200, u'data': [u'6CZxXcLcjRkrCwP6u', u'j8niawXBfvSZk85Ka', u'bhQa2YnQWKguuan9B', u'KcEcwss9bjuA4wQMR', u'yodyeFrzx7gDNzyvn', u'riDsAYcquHtfXKymg', u'M5vFYwn9ZhMj2Ljyr', u'ETfRH4vnQTnqkkJvT', u'kKzxCc5jfPHWZ6357', u'iq5eyoSGBmzasPMyz', u'27FqHpgj244GCX8ba', u's5E8ysDsTCsC3CZm8', u'7tFfqQ79EPYL7BHqE', u'qauyvKnwBTGLLyYLp', u'X5SeCQvePX5R2amxT', u'uy6sKKDvSMGLNK847', u'YgwPSy6hJcJp6ZhFh', u'jsXACtKmLd9ghrBRx', u'9HZn5YhR2YvBFbL7t', u'xQ9FGSMLAwTBQHpvD', u'L9LyCNWjGiwtj6B7P', u'uCDQNeH2GiTrL5eTt', u'f77cbbn864bD796rH', u'6r7NNbJN9JrZmp3wr', u'TWkANAc2S5Hd9pCji', u'eMMRYjsTcaB4CF54F', u'kGYkqcobKevB49zbD', u'scfWTic48KtCZSnkg', u'2dTB3WFZCGzqrgTKv', u'weWtEsq46n47HGagr', u'WPSTopEk7LTfzTfsv', u'Jnijjw9BxMTN574qG', u'G82w3XQTKN6HSCR4E', u'p3rKJ4uQejMeFwzpr', u'S4xyJy3G5GzPfZsQS', u'MD8M9TyMrGujbrSCK', u'tD6ud8SpvDxcXs9XT', u'DDvJhocvHX2StYaur', u'MwKBa93QmTWjhpRQ5', u'mbR4CyFhfSdtucqDb', u'F643GMbrP5tJ8ZZTJ', u'aqoeY9

ERROR:topogram-client:500 - Error : A topogram with the same name already exists


778 edges created.
done. Topogram has been updated. Check it at https://app.topogram.io/topograms/un7wsToJkpCCtxKA5
[{'data': {'end': '2007-05-25T19:00:00', 'target': 'axis42-71', 'weight': 1.0, 'source': 'planeta-bar-rio29-95', 'color': '#7f3f3f', 'notes': 'distance : 431.534601 km  \nsource : planeta-bar-rio29-95  target : axis42-71  \ndatesource : 2007-05-11T20:00:00  \ndatetarget : 2007-05-25T19:00:00  \ngroup: 0  \ncounted1  times', 'start': '2007-05-11T20:00:00'}}, {'data': {'end': '2007-05-26T20:00:00', 'target': 'shampoo-nightclub39-75', 'weight': 1.0, 'source': 'axis42-71', 'color': '#7f3f3f', 'notes': 'distance : 3337.082305 km  \nsource : axis42-71  target : shampoo-nightclub39-75  \ndatesource : 2007-05-25T19:00:00  \ndatetarget : 2007-05-26T20:00:00  \ngroup: 0  \ncounted1  times', 'start': '2007-05-25T19:00:00'}}, {'data': {'end': '2007-05-27T20:00:00', 'target': 'myst-nightclub33-111', 'weight': 1.0, 'source': 'shampoo-nightclub39-75', 'color': '#7f3f3f', 'notes': 'dista

...

454 nodes deleted
607 edges deleted
{u'status': u'success', 'status_code': 200, u'data': [u's4xWyuqnDTSsxCcbJ', u'GAdCaw5zZXSj3dKmD', u'XhRZShviNR9H7bsA3', u'2gPcSjuz3XCi9NgNk', u'3Kar7BuzWJjQiscbF', u'yWKzq26KsccBWRxbP', u'we4sSw7gtfTZ4FaoZ', u'QcKbtiXubwdxhANRr', u'DJAgeCQQD5dLK3Rcn', u'FjextoqLncDawFiXz', u'uqFoSYKiXW5QcxLDS', u'Pee8ZaJ7AdY7JFPy9', u'zKTPbfQWALjFvMeqv', u'czkHQ3hd4bKWkmmre', u'iAPMWKGaf6JvMNrke', u'zFHR3FQFzLQuwudTs', u'MfuiKJb6ZM8bE3QeD', u'hvMhMw9aErYogPg86', u'tsucDEYA3ihzBoo6E', u'T2mqbaD8TdLXsqjXn', u'e9vwNPxDcw7boLhjp', u'Q2gCKTiP5L6g4Jvxo', u'dEDNo9j5TMZjh9ZL4', u'qDNZ3Z7uRozFhjse8', u'AuEMofLf7HJRRmF4M', u'wqHpoEWd6aSxS47bi', u'WC7CZuWLwDyyJfsGT', u'hdwwMxiCrK83nLSH7', u'9TxmpuQuvKhr28nZG', u'CQNdfKjEvw3LEHzKQ', u'dtKiqDZQRniGLmHC3', u'bmD2F7DMDGGpWgCte', u'WNxYggf8chnnao4LF', u'WG5f7SB5AWXcGDWmt', u'5KWSzqrDPLCzGNetw', u'i2gLjPYoatGL2G9nP', u'nqaqcaHTtHMdnjgvJ', u'28TJf2ts6eSE3HbTY', u'v8AQSaZSZHrq9LpDg', u'q6dxrSQpRoDitZLTi', u'F4QJncM46yCaB84tQ', u'fqbdB7

ERROR:topogram-client:500 - Error : A topogram with the same name already exists


607 edges created.
done. Topogram has been updated. Check it at https://app.topogram.io/topograms/w4xrhv9jeqhSJq36D
[{'data': {'end': '2008-04-11T19:00:00', 'target': 'the-mod-club43-79', 'weight': 1.0, 'source': 'hiro-ballroom40-73', 'color': '#7f3f3f', 'notes': 'distance : 509.18037 km  \nsource : hiro-ballroom40-73  target : the-mod-club43-79  \ndatesource : 2008-04-10T19:00:00  \ndatetarget : 2008-04-11T19:00:00  \ngroup: 0  \ncounted1  times', 'start': '2008-04-10T19:00:00'}}, {'data': {'end': '2008-04-12T19:00:00', 'target': 'circus-afterhours45-73', 'weight': 1.0, 'source': 'the-mod-club43-79', 'color': '#7f3f3f', 'notes': 'distance : 629.987395 km  \nsource : the-mod-club43-79  target : circus-afterhours45-73  \ndatesource : 2008-04-11T19:00:00  \ndatetarget : 2008-04-12T19:00:00  \ngroup: 0  \ncounted1  times', 'start': '2008-04-11T19:00:00'}}, {'data': {'end': '2008-04-13T19:00:00', 'target': 'the-barbary39-75', 'weight': 1.0, 'source': 'circus-afterhours45-73', 'color': '#7f

{u'status': u'success', 'status_code': 200, u'data': {u'sharedPublic': False, u'title': u'Steve Aoki/BETA_0.3', u'userId': u'MSreQEjksjoK2igp5', u'_id': u'xq4CgcPhGZ49Gd9Ev', u'slug': u'steve-aokibeta_03', u'createdAt': u'2018-05-15T07:43:12.080Z'}, u'statusCode': 200}
topogram ID : xq4CgcPhGZ49Gd9Ev
855 nodes deleted
1311 edges deleted
{u'status': u'success', 'status_code': 200, u'data': [u'JQeAYD6Ch8SwF6Nzz', u'9C5eWJ2EmRtrqMRDD', u'7gXFGBE3RWgLwaP3Y', u'Fuu7ZPecvfnSEpsjN', u'8TgkRZPAmfFyKD5zo', u'bALQwFxxmTg5qrNnk', u'4KRCZpX74ff7Es9si', u'PPQBb7ZKpNskG7Tso', u'F3mooPmecKpyWmfF3', u'SzyfkTgsj6H8fHyhm', u'XZBFXJ57JiB3is5is', u'MvXSi6y3c3mZQTvTo', u'aGoweBhX4gRirwEjp', u'uCNwPrQDeF5cvkWkL', u'tgfwdEjSTdhiCMBMo', u'hHMABnaeefxwfPXSk', u'RkdsJesyuf48d8ZRx', u'Zryidz4Zcav5xaTWg', u'5Z32iSD2qHm4gA54K', u'vRwABbtX3co2bZpSC', u'dZXfSqhJd8KQhDH9p', u't4jdP6spN6ychS9Yc', u'qtXwkY4uv4LF8toBp', u'y6i4kevj4tXXjCkxW', u'YL4rSkXxnfj62Q8wG', u'WRq3QnM4orXC7tokH', u'EDvZNMynan7TdL9PW', u'uD9mXn2RWTy

1311 edges created.
done. Topogram has been updated. Check it at https://app.topogram.io/topograms/xq4CgcPhGZ49Gd9Ev
